# Парсинг. Otello
Ссылка на сайт: otello.ru

In [2]:
import requests
from bs4 import BeautifulSoup
import json

Переходим на страницу [с отелями в Москве](https://otello.ru/hotels/moskva), указываем любые параметры заселения. При просмотра исходного кода видим, что ни одного полезного тэга с указанием отелей и ссылок на их страницы  не найдено. Также в исходном коде не удалось найти js-скриптов, которые могли бы помочь в сборе информации. В панели "Сеть"инструментов разработчика поищем возможности для сбора данных. Из полезного есть только api 2gis, он не предоставляет никакой информации, кроме расположения отелей даже без указания названия.  

Рассмотрим отдельные страницы отелей. Если данные на страницах информативно и удобно извлекаемые, то возможно нам стоит не бросать этот сайт, а придумать способ собрать все ссылки на отели с главной страницы, а затем пройтись по отдельным страницам и взять все необходимое 

При изучении исходного кода страницы отеля был найден script-tag с параметром type="application/ld+json", где содержится вся информация об объекте. 

In [7]:
url = "https://otello.ru/hotel/4504127908391078"

response = requests.get(url)

soup = BeautifulSoup(response.text, 'html.parser')
    
script_tags = soup.find_all('script', type='application/ld+json')
    
    
json_data = script_tags[1].string
        
try:
    json_object = json.loads(json_data)
    print(json.dumps(json_object, indent=4, ensure_ascii=False))
except json.JSONDecodeError as e:
    print(f"Ошибка при преобразовании в JSON: {e}")


{
    "@type": "Hotel",
    "@context": "https://schema.org",
    "name": "Пекин",
    "url": "https://otello.ru/hotel/4504127908391078",
    "address": {
        "@type": "PostalAddress",
        "addressLocality": "Москва",
        "streetAddress": "Большая Садовая улица, 5",
        "addressCountry": {
            "@type": "Country",
            "name": "RU"
        }
    },
    "image": "https://i3.photo.2gis.com/photo-gallery/5b529a32-f923-4968-b667-8c66e8889ce4.jpg",
    "hasMap": "https://otello.ru/hotel/4504127908391078",
    "geo": {
        "@type": "GeoCoordinates",
        "latitude": 55.768739,
        "longitude": 37.593943
    },
    "starRating": {
        "@type": "Rating",
        "ratingValue": "4"
    },
    "aggregateRating": {
        "@type": "AggregateRating",
        "ratingValue": 4.6,
        "ratingCount": 1060,
        "bestRating": 5,
        "worstRating": 1
    },
    "checkinTime": "14:00",
    "checkoutTime": "12:00",
    "description": "Отель Пекин 4*

Данная особенность сайта значительно упрощает работу при парсинге. Действительно, стоит остановиться  именно на otello и попробовать отыскать способ заполучить все ссылки на отели. 

Внимательный осмотр сайта помог решить проблему с поиском отелей по сайту. На сайте существует рекомендательная система - на каждый странице отеля можно найти отели рядом с похожим рейтингом. Получается, мы можем как составитель датасета из гп-1 воспользоваться встроенной системой рекомендации и выкачать столько данных, сколько нам нужно. Но мы будем действовать немного хитрее и не будем напрямую выискивать в html-коде (тем более их там непросто достать), а воспользуемся открытым API сайта, который отвечает за систему рекомендации. 

```bash
curl 'https://otello-fluidsearch.api.2gis.com/api/v3/offers?rating=4.1&stars=3,4,5&price=4406,6610&limit=11&adult_count=2&checkin_date=2025-03-08&checkout_date=2025-03-09&bbox=37.56196908716482,55.75075256788162,37.62591691283519,55.78672543211836&zoom=10&sort=popular' \
  -H 'accept: application/json, text/plain, */*' \
  -H 'accept-language: ru,en;q=0.9,en-GB;q=0.8,en-US;q=0.7' \
  -H 'origin: https://otello.ru' \
  -H 'priority: u=1, i' \
  -H 'referer: https://otello.ru/' \
  -H 'sec-ch-ua: "Not(A:Brand";v="99", "Microsoft Edge";v="133", "Chromium";v="133"' \
  -H 'sec-ch-ua-mobile: ?0' \
  -H 'sec-ch-ua-platform: "Windows"' \
  -H 'sec-fetch-dest: empty' \
  -H 'sec-fetch-mode: cors' \
  -H 'sec-fetch-site: cross-site' \
  -H 'user-agent: Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/133.0.0.0 Safari/537.36 Edg/133.0.0.0' \
  -H 'x-otello-ab-test: nearestAvailableDates=nearestdates_2;welcomePackAndInspirationFeed=inspirationFeed_2' \
  -H 'x-otello-operation-stack: frontend-client-desktop.similar_hotels' \
  -H 'x-otello-platform: other_web' \
  -H 'x-request-id: eff3a817-b46e-47f8-bf2f-d8fe3561c19e' \
  -H 'x-user-id: 05c84678-75b0-4d28-9b6c-9b437d50c198'
```

Из наиболее интересного можно заметить, что в параметрах указывается рейтинг, число звезд и цена. Но самый важный параметр, на который нужно обратить особое внимание - bbox. Как не сложно догадаться, данный параметр задает радиус поиска похожих отелей. То есть в запросе выше это координаты отеля +- заданное значение. Нам, естественно, нужно как можно сильнее расширить радиус поиска отелей. Также нужно изменить другие параметры
* увеличив параметр limit - максимальное число результатов поиска
* добавить все звезды отелей - чтобы попадались все доступные отели 
* рассмотреть, какие бывают рейтинги и пройтись по им всем (указать все рейтинги через запятую как со звездами не получится - сервер выдаст ошибку)

```bash

In [56]:
import requests

url = "https://otello-fluidsearch.api.2gis.com/api/v3/offers"
params = {
    "rating": 3,
    "stars": "1,2,3,4,5",
    "limit": 1000,
    "adult_count": 2,
    "checkin_date": "2025-02-27",
    "checkout_date": "2025-02-28",
    "bbox": "37.33250000000000,55.56150000000000,37.89500000000000,55.91700000000000",
    "zoom": 1,
    "sort": "popular"
}
headers = {
    "accept": "application/json, text/plain, */*",
    "accept-language": "ru,en;q=0.9,en-GB;q=0.8,en-US;q=0.7",
    "origin": "https://otello.ru",
    "priority": "u=1, i",
    "referer": "https://otello.ru/",
    "user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/133.0.0.0 Safari/537.36 Edg/133.0.0.0",
    "x-request-id": "ae29a3e1-3dc7-441d-8bcb-b5e63845da8e",
    "x-user-id": "05c84678-75b0-4d28-9b6c-9b437d50c198"
}

response = requests.get(url, headers=headers, params=params)

json_object = response.json()
print(json.dumps(json_object, indent=4, ensure_ascii=False))


{
    "payload": {
        "details": {
            "booking_params": {
                "adult_count": 2,
                "checkin": "2025-02-27",
                "checkout": "2025-02-28",
                "children": [],
                "guest_groups": [
                    {
                        "adults": 2
                    }
                ]
            },
            "total_items": 463,
            "total_processed": 838
        },
        "items": [
            {
                "accommodation_type": {
                    "code": "hotel",
                    "label": "Отель"
                },
                "address": {
                    "adm_div": [
                        "5349042514588558",
                        "4504222397630173",
                        "4504209512726536"
                    ],
                    "building_id": "4504235282810606",
                    "city": "Москва",
                    "main_adm_div": "4504222397630173",
                    "na

In [57]:
print(len(json_object['payload']['items']))
for match in json_object['payload']['items']:
    print(match['id'])

463
70000001006921536
4504127908618658
4504127908391078
70000001088806149
4504127908370074
4504127908381626
70000001050202311
4504127908366865
4504127908386113
4504127908370716
4504127908370115
4504127908367336
70000001083276294
70000001028361769
4504127908393745
4504127908384638
4504128908954403
4504127908386571
4504127916068936
70000001043760065
70000001046692395
4504127908825059
70000001081182600
4504127908366838
70000001030048533
70000001019724543
70000001057729636
70000001033435399
70000001018805432
70000001084444717
4504127908393848
70000001075949237
70000001029175313
70000001043985143
4504127918263819
70000001035496190
70000001048033562
70000001019177776
4504127908367342
70000001032491025
70000001063005680
4504127919312146
70000001054601952
4504127909206368
70000001067802306
70000001038750468
70000001066226619
70000001027759034
70000001080855760
4504127908391137
70000001030585700
70000001043757824
4504128908695613
70000001027618961
70000001018578039
70000001054967728
70000001023

Расширение поиска до всей территории России и регулирование параметров позволило нам увеличить количество выдаваемых отелей в десятки раз. Теперь охватим всю Россию, при этом пройдемся по всем рейтингам. Результатом работы станет список ссылок всех отелей. Дальше мы будем выискивать информацию по уже написанному скрипту для парсинга отдельных страниц    

In [64]:
import requests
import json

url = "https://otello-fluidsearch.api.2gis.com/api/v3/offers"
headers = {
    "accept": "application/json, text/plain, */*",
    "accept-language": "ru,en;q=0.9,en-GB;q=0.8,en-US;q=0.7",
    "origin": "https://otello.ru",
    "priority": "u=1, i",
    "referer": "https://otello.ru/",
    "user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/133.0.0.0 Safari/537.36 Edg/133.0.0.0",
    "x-request-id": "ae29a3e1-3dc7-441d-8bcb-b5e63845da8e",
    "x-user-id": "05c84678-75b0-4d28-9b6c-9b437d50c198"
}

bbox_russia = "19.63890000000000,41.18500000000000,190.00000000000000,81.85600000000000"

hotel_links = []

for rating in range(1, 6):
    params = {
        "rating": rating,
        "stars": "1,2,3,4,5",
        "limit": 10000,
        "adult_count": 2,
        "checkin_date": "2025-02-27",
        "checkout_date": "2025-02-28",
        "bbox": bbox_russia,
        "zoom": 1,
        "sort": "popular"
    }
    
    response = requests.get(url, headers=headers, params=params)
    json_object = response.json()
    
    for match in json_object.get('payload', {}).get('items', []):
        hotel_links.append(f"https://otello.ru/hotel/{match['id']}")

print("\n".join(hotel_links))


https://otello.ru/hotel/70000001044456305
https://otello.ru/hotel/5348552838541918
https://otello.ru/hotel/70000001095724816
https://otello.ru/hotel/70000001006921536
https://otello.ru/hotel/70000001078620398
https://otello.ru/hotel/4504127908618658
https://otello.ru/hotel/4504127908391078
https://otello.ru/hotel/70000001090565839
https://otello.ru/hotel/70000001044011867
https://otello.ru/hotel/70000001079794998
https://otello.ru/hotel/70000001088806149
https://otello.ru/hotel/70000001020109401
https://otello.ru/hotel/70000001032432991
https://otello.ru/hotel/4504127908370074
https://otello.ru/hotel/4504127908381626
https://otello.ru/hotel/70000001083395184
https://otello.ru/hotel/4222653932198975
https://otello.ru/hotel/4222653931885663
https://otello.ru/hotel/70000001052979889
https://otello.ru/hotel/70000001065441010
https://otello.ru/hotel/7037402698750825
https://otello.ru/hotel/70000001006918270
https://otello.ru/hotel/70000001075058822
https://otello.ru/hotel/70000001087616127


Более 2 000 строк отелей готовы, осталось только распарсить данные и взять все необходимое. На основе предыдущего кода парсера составим функцию, принимающую ссылку отеля и добавляющую данные в датасет  

In [ ]:
# TODO
# Завернуть это все в функцию
# Добавить код для подбора нужных данных 

url = "https://otello.ru/hotel/4504127908391078"

response = requests.get(url)

soup = BeautifulSoup(response.text, 'html.parser')
    
script_tags = soup.find_all('script', type='application/ld+json')
    
    
json_data = script_tags[1].string
        
try:
    json_object = json.loads(json_data)
    print(json.dumps(json_object, indent=4, ensure_ascii=False))
except json.JSONDecodeError as e:
    print(f"Ошибка при преобразовании в JSON: {e}")
